In [15]:
import pandas as pd
from scipy.io import arff

import plotly
plotly.tools.set_credentials_file(username='artemii-yanushevskyi', api_key='aRmQfG7U4SAlhISYVym7')

import plotly.plotly as py
import plotly.graph_objs as go

from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)
from IPython.display import Image
import plotly.io as pio

import numpy as np
import seaborn as sns

from scipy.stats.stats import pearsonr
import matplotlib.pyplot as plt
colormap = plt.cm.RdBu

exporting = False

from sklearn.model_selection import train_test_split
from sklearn.utils import shuffle

from sklearn.tree import DecisionTreeClassifier
from sklearn import metrics
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import cross_val_score

from sklearn.preprocessing import OneHotEncoder

from sklearn.externals.six import StringIO  
from IPython.display import Image  
from sklearn.tree import export_graphviz
import pydotplus

from sklearn.naive_bayes import GaussianNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.dummy import DummyClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier

# Feature Processing

In [170]:
data, meta = arff.loadarff('cworkTrain.arff')
df = pd.DataFrame(data)

# convert attribute values with type "object" to regular strings
objects_df = df.select_dtypes([object]) # select only atributes of object type
stack_df = objects_df.stack() # means create one column
decoded_stack_df = stack_df.str.decode('utf-8') # decode the values in the column
decoded_objects_df = decoded_stack_df.unstack() # separate into columns

# replace in df
for col in decoded_objects_df.columns:
    df[col] = decoded_objects_df[col]

# replace month with a value
df['month'] = pd.to_datetime(df.month, format='%b').dt.month
df['termDeposit'] = pd.to_numeric(df['termDeposit'].apply(lambda x: 0 if x == 'no' else 1))
df['poutcome'] = pd.to_numeric([0 if x=='unknown' else 1 if x=='success' else -1 for x in df['poutcome']])

In [171]:
def plotattributes(df, attributes=['balance', 'newbalance']):
    for atr in attributes:
        trace0 = go.Histogram(
            x=df[df['termDeposit'] == 0][atr],
            name='No subscribtion',
            marker=dict(color='red'),
        )
        trace1 = go.Histogram(
            x=df[df['termDeposit'] == 1][atr],
            name='Subscribtion',
            marker=dict(color='green'),
        )
        data = [trace0, trace1]
        layout = go.Layout(barmode='stack', title=atr.capitalize())
        fig = go.Figure(data=data, layout=layout)
        static_image_bytes = pio.to_image(fig, format='png')
        if exporting == True:
            display(Image(static_image_bytes))
        else:
            display(iplot(fig))

# Balance

In [172]:
plotattributes(df, ['balance'])

None

## Apply square root to ```balance``` attribute.

In [173]:
df_new = pd.DataFrame(df['termDeposit'])

df_new['balance sqrt'] = np.sign(df['balance'])*np.sqrt(np.sign(df['balance'])*df['balance'])
plotattributes(df_new, ['balance sqrt'])

None

## Apply logarithm to ```balance``` attribute.

In [199]:
x = np.linspace(-1000, 1000, num=1000)
y = signn(x) * np.log(1 + np.abs(x))
              
trace1 = go.Scatter(x=x, y=y, marker={'color': 'red', 'symbol': 104}, 
                    mode="markers+lines",  text=["one","two","three"], name='1st Trace')
                                               
data=go.Data([trace1])
layout=go.Layout(title="First Plot", xaxis={'title':'x1'}, yaxis={'title':'x2'})
figure=go.Figure(data=data,layout=layout)
iplot(figure, filename='pyguide_1')

/anaconda3/lib/python3.6/site-packages/plotly/graph_objs/_deprecations.py:39: DeprecationWarning:

plotly.graph_objs.Data is deprecated.
Please replace it with a list or tuple of instances of the following types
  - plotly.graph_objs.Scatter
  - plotly.graph_objs.Bar
  - plotly.graph_objs.Area
  - plotly.graph_objs.Histogram
  - etc.




In [174]:
signn = np.vectorize(lambda x: -1 if x<0 else 1)

In [175]:
x = df['balance']
df_new['balance log'] = signn(x) * np.log(1 + np.abs(x))
plotattributes(df_new, ['balance log'])

None

Balance is not usually well reported. The people may have big balance but in some other bank. Let's predict balance using linear regression. Let's try to predict balance in case it is zero.
The same should be done with poutcome...

In [176]:
y = df[df['balance'] != 0].drop('balance', axis=1)
X = df[df['balance'] != 0][['balance']]
y.describe()

age           day         month      duration      campaign  \
count  33366.000000  33366.000000  33366.000000  33366.000000  33366.000000   
mean      40.775850     15.756279      6.113409    257.933615      2.746149   
std       10.614692      8.312469      2.415079    256.785020      3.028759   
min       18.000000      1.000000      1.000000      0.000000      1.000000   
25%       32.000000      8.000000      5.000000    103.000000      1.000000   
50%       39.000000     16.000000      6.000000    181.000000      2.000000   
75%       48.000000     21.000000      8.000000    318.000000      3.000000   
max       94.000000     31.000000     12.000000   4918.000000     63.000000   

              pdays      previous   termDeposit  
count  33366.000000  33366.000000  33366.000000  
mean      41.125217      0.590421      0.118504  
std      101.229518      2.433856      0.323209  
min       -1.000000      0.000000      0.000000  
25%       -1.000000      0.000000      0.000000  
50%       -1.000000      0.000000      0.000000  
75%       -1.000000      0.000000      0.000000  
max      871.000000    275.000000      1.000000

In [190]:
df.head()

age           job  marital  education default  balance housing loan  \
0  58.0    management  married   tertiary      no   2143.0     yes   no   
1  44.0    technician   single  secondary      no     29.0     yes   no   
2  33.0  entrepreneur  married  secondary      no      2.0     yes  yes   
3  47.0   blue-collar  married    unknown      no   1506.0     yes   no   
4  35.0    management  married   tertiary      no    231.0     yes   no   

   contact  day  month  duration  campaign  pdays  previous  poutcome  \
0  unknown  5.0      5     261.0       1.0   -1.0       0.0        -1   
1  unknown  5.0      5     151.0       1.0   -1.0       0.0        -1   
2  unknown  5.0      5      76.0       1.0   -1.0       0.0        -1   
3  unknown  5.0      5      92.0       1.0   -1.0       0.0        -1   
4  unknown  5.0      5     139.0       1.0   -1.0       0.0        -1   

   termDeposit  
0            0  
1            0  
2            0  
3            0  
4            0

In [184]:
from sklearn.linear_model import LinearRegression

reg = LinearRegression().fit(df[df['balance'] != 0].drop('balance', axis=1).values, df[df['balance'] != 0]['balance'])
reg.score(X, y), reg.coef_, reg.intercept_, reg.predict(df[df['balance'] == 0].drop('balance', axis=1))

ValueError: could not convert string to float: 'other'

Application of logarithm would be more suitable. We can now clearly see that values above and below 0 seem to be normally distributed. This may significantly benefit some classification algorithms like Logistic Regression, although it will have no effect for Decision Tree classifier.

On the other hand, it is easier to see how to apply binning for the attribute: -9 -3 1 4.5 9.5.

We may divide data into two parts for training.

These transformations would result in some improvement if we will create 3 new attributes:
log(x) =,<,> 0 

In [75]:
df['balance_zero'] = [1 if -20 < x < 20 else 0 for x in df['balance']]

## (Later)

In [9]:
from sklearn.utils import shuffle
from sklearn.model_selection import train_test_split
df_shuffle = shuffle(df_one_hot_ordered)
X_train, X_test, y_train, y_test = train_test_split(df_shuffle.drop('termDeposit', axis=1), df_shuffle['termDeposit'], test_size=0.33, random_state=45)
display(X_train.shape, y_train.shape)

(24233, 40)

(24233,)

In [11]:
# create dummy variables for df_categorical
from sklearn.preprocessing import OneHotEncoder

df_one_hot = pd.concat([df_numerical, df['termDeposit']], axis=1)
catergorical_attributes = dict()
for atr in df_categorical.columns:
    df_dummies = pd.get_dummies(df[atr], prefix = atr)
    catergorical_attributes[atr] = [col.split('_')[1] for col in df_dummies.columns]
    df_one_hot = pd.concat([df_one_hot, df_dummies], axis=1) # the dataset ready to appy decision tree algorithm

attribute_order_one_hot = []
for i in range(len(df.columns)):
    if df.columns[i] in catergorical_attributes.keys():
        categories = [df.columns[i] + '_' + cat for cat in catergorical_attributes[df.columns[i]]]
        attribute_order_one_hot.extend(categories)
    else:
        attribute_order_one_hot.append(df.columns[i])
        
df_one_hot_ordered = df_one_hot[attribute_order_one_hot]
df_one_hot_ordered.head()

age  job_admin.  job_blue-collar  job_entrepreneur  job_housemaid  \
0  58.0           0                0                 0              0   
1  44.0           0                0                 0              0   
2  33.0           0                0                 1              0   
3  47.0           0                1                 0              0   
4  35.0           0                0                 0              0   

   job_management  job_retired  job_self-employed  job_services  job_student  \
0               1            0                  0             0            0   
1               0            0                  0             0            0   
2               0            0                  0             0            0   
3               0            0                  0             0            0   
4               1            0                  0             0            0   

   ...  month  duration  campaign  pdays  previous  poutcome_failure  \
0  ...      5     261.0       1.0   -1.0       0.0                 0   
1  ...      5     151.0       1.0   -1.0       0.0                 0   
2  ...      5      76.0       1.0   -1.0       0.0                 0   
3  ...      5      92.0       1.0   -1.0       0.0                 0   
4  ...      5     139.0       1.0   -1.0       0.0                 0   

   poutcome_other  poutcome_success  poutcome_unknown  termDeposit  
0               0                 0                 1            0  
1               0                 0                 1            0  
2               0                 0                 1            0  
3               0                 0                 1            0  
4               0                 0                 1            0  

[5 rows x 41 columns]